In [50]:
import sqlite3
import pandas as pd
import numpy as np
from datetime import datetime
from sklearn.tree import DecisionTreeRegressor 
from sklearn.linear_model import LinearRegression 
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error 
from xgboost import XGBRegressor
from math import sqrt

In [3]:
data = sqlite3.connect('database.sqlite')

In [4]:
player_data = pd.read_sql_query("SELECT * FROM Player_Attributes", data)

In [5]:
player_data.head()

id  player_fifa_api_id  player_api_id                 date  overall_rating  \
0   1              218353         505942  2016-02-18 00:00:00            67.0   
1   2              218353         505942  2015-11-19 00:00:00            67.0   
2   3              218353         505942  2015-09-21 00:00:00            62.0   
3   4              218353         505942  2015-03-20 00:00:00            61.0   
4   5              218353         505942  2007-02-22 00:00:00            61.0   

   potential preferred_foot attacking_work_rate defensive_work_rate  crossing  \
0       71.0          right              medium              medium      49.0   
1       71.0          right              medium              medium      49.0   
2       66.0          right              medium              medium      49.0   
3       65.0          right              medium              medium      48.0   
4       65.0          right              medium              medium      48.0   

   ...  vision  penalties  marking  standing_tackle  sliding_tackle  \
0  ...    54.0       48.0     65.0             69.0            69.0   
1  ...    54.0       48.0     65.0             69.0            69.0   
2  ...    54.0       48.0     65.0             66.0            69.0   
3  ...    53.0       47.0     62.0             63.0            66.0   
4  ...    53.0       47.0     62.0             63.0            66.0   

   gk_diving  gk_handling  gk_kicking  gk_positioning  gk_reflexes  
0        6.0         11.0        10.0             8.0          8.0  
1        6.0         11.0        10.0             8.0          8.0  
2        6.0         11.0        10.0             8.0          8.0  
3        5.0         10.0         9.0             7.0          7.0  
4        5.0         10.0         9.0             7.0          7.0  

[5 rows x 42 columns]

In [29]:
categorical_attributes = ['preferred_foot', 'attacking_work_rate', 'defensive_work_rate']

numercial_attributes = ['potential', 'crossing', 'finishing', 'heading_accuracy',
       'short_passing', 'volleys', 'dribbling', 'curve', 'free_kick_accuracy',
       'long_passing', 'ball_control', 'acceleration', 'sprint_speed',
       'agility', 'reactions', 'balance', 'shot_power', 'jumping', 'stamina',
       'strength', 'long_shots', 'aggression', 'interceptions', 'positioning',
       'vision', 'penalties', 'marking', 'standing_tackle', 'sliding_tackle',
       'gk_diving', 'gk_handling', 'gk_kicking', 'gk_positioning',
       'gk_reflexes']

target_attribute = ['overall_rating']

In [12]:
player_data.dropna(thresh=5, inplace=True)

In [15]:
def generate_file_name(filename):
    now = datetime.now()
    current = now.strftime("%d_%m_%Y-%H_%M_%S")
    return now.strftime("%d_%m_%Y-%H_%M_%S")+ '_' + filename

In [17]:
from clean_and_merge import Clean_and_Merge


In [18]:
custom_attribute_object = Clean_and_Merge()

merged_player_data = custom_attribute_object.fit_transform(player_data)

/Users/jithinharidas/Documents/projects/football_player_performance/clean_and_merge.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  new_df = new_df.append(temp_df)
/Users/jithinharidas/Documents/projects/football_player_performance/clean_and_merge.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  new_df = new_df.append(temp_df)
/Users/jithinharidas/Documents/projects/football_player_performance/clean_and_merge.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  new_df = new_df.append(temp_df)
/Users/jithinharidas/Documents/projects/football_player_performance/clean_and_merge.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  

In [21]:
from clean_and_merge_target import Clean_and_Merge_Target

In [22]:
merged_target_object = Clean_and_Merge_Target()
merged_target_data = merged_target_object.fit_transform(player_data)

/Users/jithinharidas/Documents/projects/football_player_performance/clean_and_merge_target.py:28: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  new_df = new_df.append(temp_df)
/Users/jithinharidas/Documents/projects/football_player_performance/clean_and_merge_target.py:28: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  new_df = new_df.append(temp_df)
/Users/jithinharidas/Documents/projects/football_player_performance/clean_and_merge_target.py:28: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  new_df = new_df.append(temp_df)
/Users/jithinharidas/Documents/projects/football_player_performance/clean_and_merge_target.py:28: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. U

In [26]:
X_train, X_test, y_train, y_test = train_test_split(merged_player_data,merged_target_data,test_size=0.20,random_state = 100)

In [27]:
from sklearn.pipeline import Pipeline
from sklearn.compose import ColumnTransformer
from sklearn.preprocessing import StandardScaler
from sklearn.preprocessing import OneHotEncoder
from sklearn.impute import SimpleImputer

In [30]:
num_pipeline = Pipeline([
    ('num_imputer', SimpleImputer(strategy='mean')), 
    ('num_scaler', StandardScaler())
])

cat_pipeline = Pipeline([
    ('cat_imputer', SimpleImputer(strategy='most_frequent')), 
    ('cat_encoder', OneHotEncoder(handle_unknown='ignore'))
])

full_transformer = ColumnTransformer([
    ('num_transformer', num_pipeline, numercial_attributes),
    ('cat_transformer', cat_pipeline, categorical_attributes)
])

target_pipeline = Pipeline([
    ('num_imputer', SimpleImputer(strategy='mean', add_indicator=True)), 
    ('num_scaler', StandardScaler())
])

In [31]:
full_transformed_data = full_transformer.fit_transform(X_train)

In [32]:
full_transformed_target = target_pipeline.fit_transform(pd.DataFrame(y_train))

In [33]:
import joblib
import os

In [34]:
dir_name = 'pipelines'
if not os.path.isdir(dir_name):
    os.makedirs(dir_name)
    
    
joblib.dump(custom_attribute_object, os.path.join(dir_name, generate_file_name('custom_attribute_object.pkl')))
joblib.dump(merged_target_object, os.path.join(dir_name, generate_file_name('merged_target_object.pkl')))    
joblib.dump(full_transformer, os.path.join(dir_name, generate_file_name('full_transformer.pkl')))
joblib.dump(target_pipeline, os.path.join(dir_name, generate_file_name('target_pipeline.pkl')))

['pipelines/19_05_2022-12_11_07_target_pipeline.pkl']

In [35]:
from sklearn.model_selection import cross_val_score

In [37]:
%%time

lin_reg = LinearRegression()

cross_val_score(estimator=lin_reg, X=full_transformed_data,
               y=full_transformed_target, cv=10, n_jobs=-1)

CPU times: user 26.8 ms, sys: 74.8 ms, total: 102 ms
Wall time: 2.14 s


array([0.85423303, 0.86729611, 0.88047406, 0.86718729, 0.87492617,
       0.85968723, 0.87449595, 0.86218802, 0.85924241, 0.86096576])

In [38]:
%%time

tree_reg = DecisionTreeRegressor()

cross_val_score(estimator=tree_reg, X=full_transformed_data,
               y=full_transformed_target, cv=10, n_jobs=-1)

CPU times: user 9.18 ms, sys: 5.6 ms, total: 14.8 ms
Wall time: 995 ms


array([0.85961748, 0.86151471, 0.86790006, 0.86715826, 0.86757686,
       0.85771535, 0.85723283, 0.84895041, 0.87642407, 0.8680465 ])

In [39]:
%%time

from sklearn.svm import SVR

svm_reg = SVR()

cross_val_score(estimator=svm_reg, X=full_transformed_data,
               y=full_transformed_target, cv=10, n_jobs=-1)

/Users/jithinharidas/Documents/projects/football_player_performance/venv/lib/python3.8/site-packages/sklearn/utils/validation.py:1107: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
/Users/jithinharidas/Documents/projects/football_player_performance/venv/lib/python3.8/site-packages/sklearn/utils/validation.py:1107: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
/Users/jithinharidas/Documents/projects/football_player_performance/venv/lib/python3.8/site-packages/sklearn/utils/validation.py:1107: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
/Users/jithinharidas/Documen

CPU times: user 13.8 ms, sys: 7.76 ms, total: 21.5 ms
Wall time: 4.1 s


array([0.97008249, 0.9790143 , 0.97592107, 0.97964019, 0.97999463,
       0.97479957, 0.97756524, 0.97552187, 0.97968291, 0.97735296])

In [47]:
%%time

xgb_reg = XGBRegressor()

cross_val_score(estimator=xgb_reg, X=full_transformed_data,
               y=full_transformed_target, cv=10, n_jobs=-1)

CPU times: user 10.8 ms, sys: 4.45 ms, total: 15.2 ms
Wall time: 7.81 s


array([0.95414568, 0.95953417, 0.96193369, 0.96236451, 0.95889084,
       0.95597493, 0.95805333, 0.95950478, 0.9610078 , 0.95705543])

In [48]:
test_data = full_transformer.transform(X_test)

In [51]:
best_model_details = {}
lin_reg.fit(X=full_transformed_data, y=full_transformed_target)

y_pred = lin_reg.predict(test_data)
y_pred = y_pred.reshape(-1, 1)

test_target = target_pipeline.transform(pd.DataFrame(y_test))

error = sqrt(mean_squared_error(y_pred=y_pred, y_true=test_target))
print('Error : ', error)

best_model_details[lin_reg] = error

Error :  0.3579794339603004


In [52]:
xgb_reg.fit(X=full_transformed_data, y=full_transformed_target)

y_pred = xgb_reg.predict(test_data)
y_pred = y_pred.reshape(-1, 1)

test_target = target_pipeline.transform(pd.DataFrame(y_test))

error = sqrt(mean_squared_error(y_pred=y_pred, y_true=test_target))
print('Error : ', error)

best_model_details[xgb_reg] = error

Error :  0.2022247954182729


In [53]:
best_model_details

{LinearRegression(): 0.3579794339603004,
 XGBRegressor(base_score=0.5, booster='gbtree', callbacks=None,
              colsample_bylevel=1, colsample_bynode=1, colsample_bytree=1,
              early_stopping_rounds=None, enable_categorical=False,
              eval_metric=None, gamma=0, gpu_id=-1, grow_policy='depthwise',
              importance_type=None, interaction_constraints='',
              learning_rate=0.300000012, max_bin=256, max_cat_to_onehot=4,
              max_delta_step=0, max_depth=6, max_leaves=0, min_child_weight=1,
              missing=nan, monotone_constraints='()', n_estimators=100, n_jobs=0,
              num_parallel_tree=1, predictor='auto', random_state=0, reg_alpha=0,
              reg_lambda=1, ...): 0.2022247954182729}

In [54]:
min_value = list(best_model_details.values())[0]
my_model = ''

In [55]:
for key, value in best_model_details.items():
    if value < min_value:
        min_value = value
        my_model = key
        
print('Best performing model : {} \nError : {}'.format(my_model, min_value))

Best performing model : XGBRegressor(base_score=0.5, booster='gbtree', callbacks=None,
             colsample_bylevel=1, colsample_bynode=1, colsample_bytree=1,
             early_stopping_rounds=None, enable_categorical=False,
             eval_metric=None, gamma=0, gpu_id=-1, grow_policy='depthwise',
             importance_type=None, interaction_constraints='',
             learning_rate=0.300000012, max_bin=256, max_cat_to_onehot=4,
             max_delta_step=0, max_depth=6, max_leaves=0, min_child_weight=1,
             missing=nan, monotone_constraints='()', n_estimators=100, n_jobs=0,
             num_parallel_tree=1, predictor='auto', random_state=0, reg_alpha=0,
             reg_lambda=1, ...) 
Error : 0.2022247954182729


In [56]:
dir_name = 'models'
if not os.path.isdir(dir_name):
    os.makedirs(dir_name)
    
joblib.dump(my_model, os.path.join(dir_name, generate_file_name('best_model.pkl')))

['models/19_05_2022-12_23_45_best_model.pkl']